In [1]:
import pandas as pd
import plotly.express as px

In [3]:
# Load the merged Excel data
merged_df = pd.read_excel('gtd_total_data_clean.xlsx')

# Calculate the attack count for each location
location_counts = merged_df['location'].value_counts().reset_index()
location_counts.columns = ['location', 'attack_count']

# Merge the attack count data with the merged dataframe
merged_df = merged_df.merge(location_counts, on='location')

# Create a scatter geo map with markers for each attack location
fig = px.scatter_geo(merged_df, lat='latitude', lon='longitude', hover_name='location', color='attack_count',
                     projection='natural earth')

# Update layout settings for the map
fig.update_layout(title='World Map of Attacks Over Time',
                  geo=dict(showcountries=True, countrycolor='gray'))

# Show the map
fig.show()



In [104]:
import pandas as pd
import folium
from folium.plugins import HeatMap

# Load the dataset
df = pd.read_excel('gtd_total_data_clean.xlsx')

# Filter attacks from the last ten years
df['iyear'] = pd.to_datetime(df['iyear'], format='%Y')
fifteen_years_ago = pd.Timestamp.now().normalize() - pd.DateOffset(years=15)
last_15_years = df[df['iyear'] >= fifteen_years_ago]

# Group the attacks by city
city_attacks = last_15_years['city'].value_counts().reset_index()
city_attacks.columns = ['city', 'attack_count']

# Merge city_attacks with df to get latitude and longitude
merged_df = pd.merge(city_attacks, df[['city', 'latitude', 'longitude']], on='city')

# Filter out rows with missing location values
merged_df = merged_df.dropna(subset=['latitude', 'longitude'])

# Create a map centered on the world
mymap = folium.Map(location=[0, 0], zoom_start=2, control_scale=True, prefer_canvas=True, tiles='CartoDB positron')

# Generate a list of (latitude, longitude, weight) tuples for the HeatMap
heat_data = merged_df[['latitude', 'longitude', 'attack_count']].values.tolist()

# Add the HeatMap layer to the map
HeatMap(heat_data).add_to(mymap)

# Save the map as an HTML file
mymap.save('terrorist_attacks_map_last15years.html')



In [96]:
import pandas as pd

# Read the dataset into a pandas DataFrame
data = pd.read_excel('gtd_total_data_clean.xlsx')

# Select the required columns
columns = ['iyear', 'country_txt']

# Filter the dataset to include only the attacks in the last 15 years
current_year = pd.Timestamp.now().year
filtered_data = data[data['iyear'] >= current_year - 15][columns]

# Group the data by 'country_txt' and count the number of attacks
grouped_data = filtered_data.groupby('country_txt').size().reset_index(name='num_attacks')

# Sort the countries based on the number of attacks in descending order
sorted_data = grouped_data.sort_values('num_attacks', ascending=False)

# Display the countries with the most attacks in the last 15 years
print(sorted_data.head(20))


                          country_txt  num_attacks
68                               Iraq        24964
0                         Afghanistan        19215
110                          Pakistan        13092
65                              India         9757
159                             Yemen         6160
115                       Philippines         5871
108                           Nigeria         5778
128                           Somalia         5082
143                          Thailand         3272
139                             Syria         2993
86                              Libya         2498
43                              Egypt         2180
30                           Colombia         2044
149                           Ukraine         1796
146                            Turkey         1791
36   Democratic Republic of the Congo         1585
121                            Russia         1262
157          West Bank and Gaza Strip         1133
151                    United K